### Quantum Molecular Collision Theory Pset 

In [0]:
import numpy as np
import pandas as pd
import sympy as sp
import plotly.graph_objects as go
import matplotlib.pyplot as plt

from typing import List
from numpy import exp
from numpy.linalg import inv

import ipywidgets as widgets
from IPython.display import display

pd.set_option('display.float_format', lambda x: "{:e}".format(x))

### problem 1

In [0]:
def problem1(m : np.double, E : np.double, V0 : np.double, a : np.double, xmin, xmax, points,
             flatten : bool=True, debug=False) -> np.array:
    """ 
        Return vector with S^{2} and R^{2} 
    """
    hbar_squared = hbar * hbar
    
    # common terms for both cases
    k = np.sqrt(2 * m * E / hbar_squared)
    M_L = np.array([[1, 1], 
                    [1j * k, -1j * k]])

    # if given energy is greater than energy of potential barrier
    if E > V0:
        kp = np.sqrt(2 * m * (E - V0) / hbar_squared)
        M_R = np.array([[1, 1],
                        [1j * kp, -1j * kp]])
        
        M_dash = np.array([[exp(1j * kp * a), exp(-1j * kp * a)],
                           [1j * kp * exp(1j * kp * a), -1j * kp * exp(-1j * kp * a)]])
    else:
        kappa = np.sqrt(2 * m * (V0 - E) / hbar_squared)
        M_R = np.array([[1, 1],
                        [kappa, -kappa]])
        
        M_dash = np.array([[exp(kappa * a), exp(-kappa * a)],
                           [kappa * exp(kappa * a), -kappa * exp(-kappa * a)]])
            
    
    # @ - denotes matrix multiplication
    M  = M_dash @ inv(M_R) @ M_L
    
    # calculate vector with S and R
    A_mat = np.array([[- exp(1j * k * a), M[0][1]], 
                    [-1j * k * exp(1j * k * a), M[1][1]]])
    B_mat = np.array([[-M[0][0]],
                  [-M[1][0]]])
    
    S_R = inv(A_mat) @ B_mat
    S, R = S_R.reshape(-1)
    
    # S_R is vector of complex number. multiplying by conjegute of it, will give us square of amplitude
    # * -  here is as broadcast operator
    amplitudes_squared = S_R * np.conjugate(S_R)
    
    
    # construct wavefunction
    # 
    A_B = inv(M_R) @ M_L @ np.array([[1],
                                      [R]])
    A_coeff, B_coeff = A_B.reshape(-1)
    
    if debug:
        print("M_R matrix")
        print(M_R)
        print("inverse of M_R")
        print(inv(M_R))
        print("M_L matrix")
        print(M_L)
        print("Refraction coeffient")
        print(R)
        print("A and B coefs")
        print(A_coeff, B_coeff)
    
    x = np.linspace(xmin, xmax, points)
    y = np.zeros(x.shape, dtype=complex)
    

    y[x < 0] = np.exp(1j * k * x[x < 0]) + R * np.exp(-1j * k * x[x < 0])
    y[x > a] = S * np.exp(1j * k * x[x > a])
    selec = np.logical_and(x >= 0, x <= a)
    if E > V0:
        y[selec] = A_coeff * np.exp(1j * kp * x[selec]) + B_coeff * np.exp(-1j * kp * x[selec])
    else:
        y[selec] = A_coeff * np.exp(kappa * x[selec]) + B_coeff * np.exp(-kappa * x[selec])
    
    
    # flattening vector from 1x2 to 2
    if flatten:
        return np.real(amplitudes_squared.reshape(-1)), (x,y)
    return np.real(amplitudes_squared), (x, y)

In [0]:
def calculate_coefficients(energies : List, m : np.double, V0 : np.double, a : np.double, return_raw:bool =False,
                           plot=False, xmin=-10, xmax=10, points=1000, scaling_factor=2000, debug=False):
    # Test coefficient calculation and show results 
    raw = np.array([]).reshape(-1, 3)
    
    if plot:
        fig = go.Figure()
        x = np.linspace(xmin, xmax, points)
        y = np.zeros(x.shape)
        y[np.logical_and(x >= 0, x <= a)] = V0 * scaling_factor
        fig.add_trace(go.Scatter(x=x,y=y, name="potential"))
    
    i = 0
    for E in energies:
    
        # actual calcultions of energies 
        energies, wf = problem1(m=m, E=E, V0=V0, a=a, xmin=xmin, xmax=xmax, points=points, debug=debug)

        # do some reshaping magic to pretty print later
        raw = np.concatenate([raw, np.concatenate([np.array([E]), energies]).reshape(-1, 3)], axis=0)
        
        if plot:
            fig.add_trace(go.Scatter(x=wf[0], y=np.real(wf[1]),name="$real(\psi_{" + str(i) + "})$"))
            fig.add_trace(go.Scatter(x=wf[0], y=np.imag(wf[1]),name="$imag(\psi_{" + str(i) + "})$"))
            
        i += 1

    if plot:
        fig.show()

    # represented as matrix n x 3  [n - number of energies ]
    # 0 column are energies,
    # 1 column are S^{2}
    # 2 column are E^{2}
    if return_raw:
        return raw, wf
    
    # return dataframe
    return pd.DataFrame(raw, columns=['Energy', "$S^{2}$", "$R^{2}$"]), wf 

In [0]:
energies_requested = [4.1e-4, 8.1e-4, 1.21e-3, 1.61e-3, 2.01e-3]
m  = 1822
V0 = 8 * 10**-4
a  = 3 
hbar=1

dataframe, wf_rect = calculate_coefficients(energies=energies_requested, m=m, V0=V0, a=a, plot=True)
dataframe

Energy      $S^{2}$      $R^{2}$
0 4.100000e-04 3.124008e-03 9.968760e-01
1 8.100000e-04 1.470529e-01 8.529471e-01
2 1.210000e-03 9.249715e-01 7.502850e-02
3 1.610000e-03 9.088688e-01 9.113124e-02
4 2.010000e-03 9.999826e-01 1.741665e-05

### Problem 2

In [0]:
energies = np.linspace(1e-4, 3e-2, 30000)

df_p2, wf = calculate_coefficients(energies, m, V0, a)
fig = go.Figure()
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = np.log(df_p2["$R^{2}$"]), name="$R^{2}$"))
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = df_p2["$S^{2}$"], name="$S^{2}$"))
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = df_p2["$R^{2}$"] + df_p2["$S^{2}$"], name="$R^{2} + S^{2}$"))
fig.show()

Output hidden; open in https://colab.research.google.com to view.

### Problem 3

In [0]:
df_p3, wf = calculate_coefficients(np.linspace(1e-6, 6e-3, 30000), 50 * m, V0, a)
fig = go.Figure()
fig.add_trace(go.Scatter(x = df_p3["Energy"], y = df_p3["$R^{2}$"], name="$R^{2}$"))
fig.add_trace(go.Scatter(x = df_p3["Energy"], y = df_p3["$S^{2}$"], name="$S^{2}$"))
fig.add_trace(go.Scatter(x = df_p3["Energy"], y = df_p3["$R^{2}$"] + df_p3["$S^{2}$"], name="$R^{2} + S^{2}$"))
fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [0]:
# rect potential

rect_x = np.linspace(-10, 10, 1000)
rect_y = np.zeros(rect_x.shape)
rect_y[np.logical_and(rect_x >= 0, rect_x <= a)] = V0 * 2000

In [0]:
S_R, wf = calculate_coefficients([1e-6], 50 * m, V0, a, return_raw=True, points=10000, debug=True)
print("energy, scattering and refraction")
print(S_R)
fig = go.Figure()
fig.add_trace(go.Scatter(x=wf[0], y=np.real(wf[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf[0], y=np.imag(wf[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.show()

M_R matrix
[[  1.           1.        ]
 [ 12.06556256 -12.06556256]]
inverse of M_R
[[ 0.5         0.04144026]
 [ 0.5        -0.04144026]]
M_L matrix
[[1.+0.j         1.+0.j        ]
 [0.+0.42684892j 0.-0.42684892j]]
Refraction coeffient
(-0.9975000000000002-0.07066647012551285j)
A and B coefs
(-1.1102230246251565e-16+1.0408340855860843e-17j) (0.002499999999999891-0.07066647012551286j)
energy, scattering and refraction
[[1.0e-06 2.5e-01 1.0e+00]]


In [0]:
S_R, wf = calculate_coefficients([7.59912e-6], 50 * m, V0, a, return_raw=True, debug=True)
print(S_R)
fig = go.Figure()
fig.add_trace(go.Scatter(x=wf[0], y=np.real(wf[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf[0], y=np.imag(wf[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.show()

M_R matrix
[[  1.           1.        ]
 [ 12.01563316 -12.01563316]]
inverse of M_R
[[ 0.5         0.04161246]
 [ 0.5        -0.04161246]]
M_L matrix
[[1.+0.j         1.+0.j        ]
 [0.+1.17667313j 0.-1.17667313j]]
Refraction coeffient
(-0.9810021999999998-0.19399660717435235j)
A and B coefs
(1.1102230246251565e-16+1.3877787807814457e-17j) (0.018997800000000065-0.19399660717435238j)
[[7.59912e-06 2.08125e+01 1.00000e+00]]


In [0]:
S_R, wf = calculate_coefficients([1.21e-3], m, V0, a, return_raw=True, debug=True)
print("energy | scattering | refraction")
print(S_R)
fig = go.Figure()
fig.add_trace(go.Scatter(x=wf[0], y=np.real(wf[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf[0], y=np.imag(wf[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.show()

M_R matrix
[[1.+0.j         1.+0.j        ]
 [0.+1.22230929j 0.-1.22230929j]]
inverse of M_R
[[0.5+0.j         0. -0.40906177j]
 [0.5+0.j         0. +0.40906177j]]
M_L matrix
[[1.+0.j         1.+0.j        ]
 [0.+2.09981904j 0.-2.09981904j]]
Refraction coeffient
(0.15193271088899896-0.22791434918925957j)
A and B coefs
(1.3044185792577536+0.08181115256241046j) (-0.15248586836875472-0.30972550175167j)
energy | scattering | refraction
[[0.00121   0.9249715 0.0750285]]


### Problem 4

In [0]:
def sech(x):
    #                 broadcast operator
    return 1 / np.cosh(x) 

def eckhart_barrier(x, a, V0):
    return V0 * sech( (x*a)**2 )

V0 = 3 *10**-4
a  = 2 
start = -3
end   = 3
points = 1000


X = np.linspace(start, end, points)
fig = go.Figure()
fig.add_trace(go.Scatter(x=X, y = eckhart_barrier(x=X, a=4, V0=V0) , name="a=4"))
fig.add_trace(go.Scatter(x=X, y = eckhart_barrier(x=X, a=3, V0=V0) , name="a=3"))
fig.add_trace(go.Scatter(x=X, y = eckhart_barrier(x=X, a=2, V0=V0) ,name="a=2"))
fig.show()

## problem 5

- verify on step barrier

In [0]:
def infty(x):
    return np.exp(1j * k * x)

def infty_m(x):
    return np.exp(-1j * k * x)

def kn_squared(x, mass, E, potential):
    return 2 * mass * (E - potential(x)) / (hbar * hbar)


def numerov_bad(left : np.double, right : np.double, steps : np.int, 
            infty, potential, mass : np.double, energy : np.double):
    step = (right - left) / steps
    h = step
    wavefunction = [infty(left) ,infty(left + step)]
    linspace = np.arange(left + 2*step, right, step)
    ABs = []

    for x in linspace[2:]:
        next_coeff = 1 + h * h / 12. * kn_squared(x, mass, energy, potential)
        coeff      = 2 - 10 * h * h / 12. * kn_squared(x-step, mass, energy, potential) 
        prev_coeff = 1 + h * h / 12. * kn_squared(x- 2*step, mass, energy, potential)        
        next_wf_step = coeff * wavefunction[-1] - prev_coeff * wavefunction[-2]
        wavefunction.append(next_wf_step / next_coeff)
        
    mat = np.array([[np.exp(1j * k * linspace[-2]), np.exp(-1j * k * linspace[-2])], 
                    [np.exp(1j * k * linspace[-1]), np.exp(-1j * k * linspace[-1])]])
    ABs= np.linalg.inv(mat) @ np.array([[wavefunction[-2]], [wavefunction[-1]]])
    
    return (linspace, np.array(wavefunction),ABs)

def calculateSR_bad(AB):
    A, B = AB.reshape(-1)
    S = A - B * np.conjugate(B) / np.conjugate(A)
    R = -B / np.conjugate(A)
    return (S, (S*np.conjugate(S)).real, R, (R*np.conjugate(R)).real)

In [0]:
def P(x, m, V, E):
    return -2 * m * (V(x) - E) / hbar / hbar

def infinity_p(k, x):
    return np.exp(1j * k * x)

def infinity_m(k, x):
    return np.exp(-1j * k * x)


def numerov(x_min, x_max, points, m, V, E, start):
    grid = np.linspace(x_min, x_max, points)
    h = (x_max - x_min) / points
    
    # calculate 2 values for boundary conditions
    # to start solving recurrent equation
    wf = [start(grid[0]), start(grid[1])]
    for i in range(2, grid.shape[0]):
        coeff_plus  = 1 + h * h / 12 * P(grid[i], m, V, E)
        coeff       = 2 * (1 - 5 * h * h / 12 * P(grid[i-1], m , V, E))
        coeff_minus = (1 + h * h / 12 * P(grid[i-2], m, V, E))
        
        wf_next     =  (coeff * wf[i-1] - coeff_minus * wf[i-2]) / coeff_plus
        wf.append(wf_next)
        i += 1
    return grid, wf

def numerov_k(x_min, x_max, points, m, V, E, known1, known2):
    grid = np.linspace(x_min, x_max, points)
    h = (x_max - x_min) / points
    
    # calculate 2 values for boundary conditions
    # to start solving recurrent equation
    wf = [known1, known2]
    for i in range(2, grid.shape[0]):
        coeff_plus  = 1 + h * h / 12 * P(grid[i], m, V, E)
        coeff       = 2 * (1 - 5 * h * h / 12 * P(grid[i-1], m , V, E))
        coeff_minus = (1 + h * h / 12 * P(grid[i-2], m, V, E))
        
        wf_next     =  (coeff * wf[i-1] - coeff_minus * wf[i-2]) / coeff_plus
        wf.append(wf_next)
        i += 1
    return grid, wf


def scattering_and_refraction(grid, wf, k):
    xn  = grid[-1]
    xn_minus_1 = grid[-2]
    
    wfn = wf[-1]
    wfn_minus_1 = wf[-2]
    
    X = np.array([[np.exp(1j * k * xn_minus_1), np.exp(-1j * k * xn_minus_1)],
                  [np.exp(1j * k * xn)         , np.exp(-1j * k * xn)]])
    Y = np.array([[wfn_minus_1],
                  [wfn]])
    
    
    A,B =  (inv(X) @ Y).reshape(-1)
    
    return np.array([A - B*np.conjugate(B)/ np.conjugate(A), -B / np.conjugate(A) ])

In [0]:
def rectBarrier(x, a, V0):
    y = np.zeros(x.shape)
    y[np.logical_and(x>=0, x<=a)] = V0
    return y

def rectBarrier2(x, a, V0):
    if x < 0 or x > a:
        return 0
    return V0

### numerov method on  rectangular barrier

In [0]:
m  = 1822
V0 = 8. * 10**-4
a  = 3
E  = 11.* 10**-4
k = np.sqrt(2 * m * E / hbar / hbar)

x_min = -10
x_max =  10
steps =  10000

potential_rect = lambda x: rectBarrier2(x, a, V0)
infty_p = lambda x: infinity_p(k, x)
infty_m = lambda x: infinity_m(k, x)


rect_x = np.linspace(x_min, x_max, steps)
rect_y = rectBarrier(rect_x, a, V0*2000)

linsp_r, wf_r = numerov(x_min, x_max, steps, m, potential_rect, E, infty_p)
S_R, wf_an = calculate_coefficients([E], m, V0, a, xmin=x_min, xmax=x_max, return_raw=True, debug=False)
fig = go.Figure()
x=np.linspace(x_min, x_max, steps)
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.real(wf_an[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.imag(wf_an[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.real(wf_r), name="$real(\psi)_{N}$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.imag(wf_r), name="$imag(\psi)_{N}$"))
fig.show()

In [0]:
print(S_R[0][1:])

sr = scattering_and_refraction(linsp_r, wf_r, k)
print(np.real(sr * np.conjugate(sr)).real)

[9.99988328e-01 1.16719074e-05]
[9.99988661e-01 1.13389765e-05]


In [0]:
m  = 1822
V0 = 8. * 10**-4
a  = 3
E  = 9.* 10**-4
k = np.sqrt(2 * m * E / hbar / hbar)

x_min = -10
x_max =  10
steps =  10000

potential_rect = lambda x: rectBarrier2(x, a, V0)
infty_p = lambda x: infinity_p(k, x)
infty_m = lambda x: infinity_m(k, x)


rect_x = np.linspace(x_min, x_max, steps)
rect_y = rectBarrier(rect_x, a, V0*2000)
linsp_r, wf_rp = numerov(x_min, x_max, steps, m, potential_rect, E, infty_p)


linsp_r, wf_rm = numerov(x_min, x_max, steps, m, potential_rect, E, infty_m)
linsp_r, wf_rp = numerov(x_min, x_max, steps, m, potential_rect, E, infty_p)
S_R, wf_an = calculate_coefficients([E], m, V0, a, xmin=x_min, xmax=x_max, return_raw=True, debug=False)
fig = go.Figure()
x=np.linspace(x_min, x_max, steps)
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.real(wf_an[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.imag(wf_an[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.real(wf_rm), name="$real(\psi^{-})_{N}$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.imag(wf_rm), name="$imag(\psi^{-})_{N}$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.real(wf_rp), name="$real(\psi^{+})_{N}$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.imag(wf_rp), name="$imag(\psi^{+})_{N}$"))
fig.show()  

In [0]:
linsp_r, wf_r = numerov_k(x_min, x_max, steps, m, potential_rect, E, wf_an[1][0], wf_an[1][1])
S_R, wf_an = calculate_coefficients([E], m, V0, a, xmin=x_min, xmax=x_max, return_raw=True, debug=False)

fig = go.Figure()
x=np.linspace(x_min, x_max, steps)
fig.add_trace(go.Scatter(x=rect_x, y=rect_y,name="potential"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.real(wf_an[1]),name="$real(\psi)$"))
fig.add_trace(go.Scatter(x=wf_an[0], y=np.imag(wf_an[1]),name="$imag(\psi)$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.real(wf_r), name="$real(\psi)_{N}$"))
fig.add_trace(go.Scatter(x=linsp_r, y=np.imag(wf_r), name="$imag(\psi)_{N}$"))
fig.show()

In [0]:
print(wf_an[0][:2], wf_an[1][:2])
print(linsp_r[:2], wf_r[:2])

[-10.          -9.97997998] [1.39446834+0.23122193j 1.35305639+0.23406466j]
[-10.         -9.9979998] [(1.3944683400944813+0.23122193084100912j), (1.3530563908359092+0.2340646566516233j)]


In [0]:
m  = 1822
V0 = 8. * 10**-4
a  = 3
E  = 18.* 10**-4
k = np.sqrt(2 * m * E / hbar / hbar)

potential_eckh = lambda x: eckhart_barrier(x, a, V0)

linsp_p,wf_p = numerov(x_min, x_max, steps, m, potential_eckh, E, infty_m)
linsp_m,wf_m = numerov(x_min, x_max, steps, m, potential_eckh, E, infty_p)

fig = go.Figure()
fig.add_trace(go.Scatter(x=linsp_p, y=np.real(wf_p), name="$real(\psi^{+})$"))
fig.add_trace(go.Scatter(x=linsp_p, y=np.imag(wf_p), name="$imag(\psi^{+})$"))
fig.add_trace(go.Scatter(x=linsp_m, y=np.real(wf_m), name="$real(\psi^{-})$"))
fig.add_trace(go.Scatter(x=linsp_m, y=np.imag(wf_m), name="$imag(\psi^{-})$"))
fig.show()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: RuntimeWarning:

overflow encountered in cosh



In [0]:
fig = go.Figure()
x=np.linspace(-10,10,10000)
fig.add_trace(go.Scatter(x=x, y = potential_eckh(x), name="potential"))
fig.add_trace(go.Scatter(x=x, y=kn_squared(x,m,E,potential_eckh),name="$k^{2}_{n}$"))
fig.show()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: RuntimeWarning:

overflow encountered in cosh



In [0]:
m  = 1822
V0 = 8. * 10**-4
a  = 3
E  = 11.* 10**-4
k = np.sqrt(2 * m * E / hbar / hbar)

start_eng = 1e-4
end_eng = 3e-3
points = 400

energies = np.linspace(start_eng, end_eng, points)
df_p2, wf = calculate_coefficients(energies, m, V0, a)

es = np.linspace(start_eng, end_eng, points)
S2 = []
R2 = []

for e in es:
    potential_rect = lambda x: rectBarrier2(x, a, V0)
    rect_x = np.linspace(x_min, x_max, steps)
    rect_y = rectBarrier(rect_x, a, V0*2000)
    linsp_r, wf_rp = numerov(x_min, x_max, steps, m, potential_rect, e, infty_p)
    
    sr = scattering_and_refraction(linsp_r, wf_rp, k)
    sr2 = sr * np.conjugate(sr)
    S2.append(sr2[0].real)
    R2.append(sr2[1].real)

In [0]:
S2 = np.array(S2)
R2 = np.array(R2)

kd = (S2.reshape(-1, 1) + R2.reshape(-1, 1)).reshape(-1)
fig = go.Figure()
fig.add_trace(go.Scatter(x=es, y=S2, name="$S^{2}$"))
fig.add_trace(go.Scatter(x=es, y=R2, name="$R^{2}$"))
fig.add_trace(go.Scatter(x=es, y=kd, name="$R^{2}+S^{2}$"))
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = df_p2["$R^{2}$"], name="$R^{2}_{A}$"))
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = df_p2["$S^{2}$"], name="$S^{2}_{A}$"))
fig.add_trace(go.Scatter(x = df_p2["Energy"], y = df_p2["$R^{2}$"] + df_p2["$S^{2}$"], name="$R^{2}_{A} + S^{2}_{A}$"))
fig.show()